# The Battle of Neighborhoods

## Introduction to project

In this project, we will bw working on New Delhi dataset.
New Delhi is the Capital of India and has a population of about 2.18 crore (21.8 million). 
It has a diversity of religions and a lot of people from different parts of the country come here for work.
Is is a central hub of various business and political work.
New Delhi are used interchangeably to refer to the National Capital Territory of Delhi (NCT), these are two distinct entities, with New Delhi forming a small part of Delhi. The National Capital Region is a much larger entity comprising the entire NCT along with adjoining districts in neighboring states.

There are various types of restraunts and famous for variety of food.

In this project we will visualize hot spots and various neighboring restraunts of Delhi.


## Raw Data

To do this project, we will use the followinf data sets.

New Delhi Resturants data that contains list Locality, Resturant name,Rating along with their latitude and longitude.
 <ul>
     <li>Data source : kaggel dataset</li>
    <li>Description : This data set contains the required information. And we will use this data set to explore various locality of new delhi city.</li></ul>

The link to the data is : https://www.kaggle.com/shrutimehta/zomato-restaurants-data

## Data Creation and Gathering

Nearby places in each locality of new delhi city.
<ul><li>Data source : Fousquare API</li>
    <li>Description : By using this api we will get all the venues in each neighborhood.</li></ul>

## Procedure

- Collect the new delhi city data from Zomato kaggel dataset
- Using FourSquare API we will find all venues for each neighborhood.
- Filter out all venues that are nearby by locality.
- Using aggregative rating for each resturant to find the best places.
- Visualize the Ranking of neighborhoods using folium library(python)

# LIBRARIES

In [1]:
import types
import pandas as pd
from botocore.client import Config
import ibm_boto3
import numpy as np
import requests 
from pandas.io.json import json_normalize 
import matplotlib.cm as cm
import matplotlib.colors as colors
from sklearn.cluster import KMeans
#!conda install -c conda-forge folium=0.5.0 --yes ]
import folium 
#! pip install geocoder
import geocoder

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - folium=0.5.0


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    branca-0.4.0               |             py_0          26 KB  conda-forge
    python_abi-3.6             |          1_cp36m           4 KB  conda-forge
    openssl-1.1.1f             |       h516909a_0         2.1 MB  conda-forge
    ca-certificates-2020.4.5.1 |       hecc5488_0         146 KB  conda-forge
    vincent-0.4.4              |             py_1          28 KB  conda-forge
    altair-4.1.0               |             py_1         614 KB  conda-forge
    folium-0.5.0               |             py_0          45 KB  conda-forge
    certifi-2020.4.5.1         |   py36h9f0ad1d_0         151 KB  conda-forge
    ------------------------------------------------------------
                       

# LOADING AND FILTERING DATA

In [2]:
def __iter__(self): return 0

# @hidden_cell
# The following code accesses a file in your IBM Cloud Object Storage. It includes your credentials.
# You might want to remove those credentials before you share the notebook.
client_afe55041fc984c29ae3da0f99b4efe8b = ibm_boto3.client(service_name='s3',
    ibm_api_key_id='pJ2dhrGYPYYHS9LfyDQGvWZwfL1s2YBR8oqTO1TyymB1',
    ibm_auth_endpoint="https://iam.eu-gb.bluemix.net/oidc/token",
    config=Config(signature_version='oauth'),
    endpoint_url='https://s3.eu-geo.objectstorage.service.networklayer.com')

body = client_afe55041fc984c29ae3da0f99b4efe8b.get_object(Bucket='courseracapstone-donotdelete-pr-36wfsmf2ynohte',Key='Delhi_Data.csv')['Body']
# add missing __iter__ method, so pandas accepts body as file-like object
if not hasattr(body, "__iter__"): body.__iter__ = types.MethodType( __iter__, body )

# If you are reading an Excel file into a pandas DataFrame, replace `read_csv` by `read_excel` in the next statement.
rawdf = pd.read_csv(body,encoding='ISO-8859-1')
rawdf.head()


Restaurant ID         Restaurant Name  Country Code              City  \
0        6317637        Le Petit Souffle           162       Makati City   
1        6304287        Izakaya Kikufuji           162       Makati City   
2        6300002  Heat - Edsa Shangri-La           162  Mandaluyong City   
3        6318506                    Ooma           162  Mandaluyong City   
4        6314302             Sambo Kojin           162  Mandaluyong City   

                                             Address  \
0  Third Floor, Century City Mall, Kalayaan Avenu...   
1  Little Tokyo, 2277 Chino Roces Avenue, Legaspi...   
2  Edsa Shangri-La, 1 Garden Way, Ortigas, Mandal...   
3  Third Floor, Mega Fashion Hall, SM Megamall, O...   
4  Third Floor, Mega Atrium, SM Megamall, Ortigas...   

                                     Locality  \
0   Century City Mall, Poblacion, Makati City   
1  Little Tokyo, Legaspi Village, Makati City   
2  Edsa Shangri-La, Ortigas, Mandaluyong City   
3      SM Megamall, Ortigas, Mandaluyong City   
4      SM Megamall, Ortigas, Mandaluyong City   

                                    Locality Verbose   Longitude   Latitude  \
0  Century City Mall, Poblacion, Makati City, Mak...  121.027535  14.565443   
1  Little Tokyo, Legaspi Village, Makati City, Ma...  121.014101  14.553708   
2  Edsa Shangri-La, Ortigas, Mandaluyong City, Ma...  121.056831  14.581404   
3  SM Megamall, Ortigas, Mandaluyong City, Mandal...  121.056475  14.585318   
4  SM Megamall, Ortigas, Mandaluyong City, Mandal...  121.057508  14.584450   

                           Cuisines  ...          Currency Has Table booking  \
0        French, Japanese, Desserts  ...  Botswana Pula(P)               Yes   
1                          Japanese  ...  Botswana Pula(P)               Yes   
2  Seafood, Asian, Filipino, Indian  ...  Botswana Pula(P)               Yes   
3                   Japanese, Sushi  ...  Botswana Pula(P)                No   
4                  Japanese, Korean  ...  Botswana Pula(P)               Yes   

  Has Online delivery Is delivering now Switch to order menu Price range  \
0                  No                No                   No           3   
1                  No                No                   No           3   
2                  No                No                   No           4   
3                  No                No                   No           4   
4                  No                No                   No           4   

   Aggregate rating  Rating color Rating text Votes  
0               4.8    Dark Green   Excellent   314  
1               4.5    Dark Green   Excellent   591  
2               4.4         Green   Very Good   270  
3               4.9    Dark Green   Excellent   365  
4               4.8    Dark Green   Excellent   229  

[5 rows x 21 columns]

In [3]:
df=rawdf.loc[rawdf['City']=='New Delhi']
df.head()

Restaurant ID  Restaurant Name  Country Code       City  \
2560       18287358       Food Cloud             1  New Delhi   
2561       18216944        Burger.in             1  New Delhi   
2562         313333  Days of the Raj             1  New Delhi   
2563       18384127   Dilli Ka Dhaba             1  New Delhi   
2564            582        Govardhan             1  New Delhi   

                                                Address    Locality  \
2560                              Aaya Nagar, New Delhi  Aaya Nagar   
2561        84, Near Honda Showroom, Adchini, New Delhi     Adchini   
2562  81/3, 1st Floor, Qutub Residency, Adchini, New...     Adchini   
2563  66 A, Ground Floor, Sri Aurobindo Marg, Adchin...     Adchini   
2564  84, Adjacent Hero Motor Bike Showroom, Main Me...     Adchini   

           Locality Verbose  Longitude   Latitude  \
2560  Aaya Nagar, New Delhi   0.000000   0.000000   
2561     Adchini, New Delhi  77.196923  28.535382   
2562     Adchini, New Delhi  77.197475  28.535493   
2563     Adchini, New Delhi  77.198033  28.537547   
2564     Adchini, New Delhi  77.196924  28.535523   

                                 Cuisines  ...            Currency  \
2560                       Cuisine Varies  ...  Indian Rupees(Rs.)   
2561                            Fast Food  ...  Indian Rupees(Rs.)   
2562   North Indian, Seafood, Continental  ...  Indian Rupees(Rs.)   
2563           South Indian, North Indian  ...  Indian Rupees(Rs.)   
2564  South Indian, North Indian, Chinese  ...  Indian Rupees(Rs.)   

     Has Table booking Has Online delivery Is delivering now  \
2560                No                  No                No   
2561                No                 Yes                No   
2562               Yes                 Yes                No   
2563                No                  No                No   
2564                No                 Yes                No   

     Switch to order menu Price range  Aggregate rating  Rating color  \
2560                   No           2               0.0         White   
2561                   No           1               3.2        Orange   
2562                   No           3               3.4        Orange   
2563                   No           2               2.6        Orange   
2564                   No           2               3.4        Orange   

     Rating text Votes  
2560   Not rated     2  
2561     Average    46  
2562     Average    45  
2563     Average    11  
2564     Average   238  

[5 rows x 21 columns]

In [4]:
rdf= df[df.Longitude !=0.000000][['Restaurant Name','Locality','Longitude','Latitude','Cuisines','Aggregate rating','Rating text','Votes']]
rdf = rdf[rdf['Aggregate rating'] !=0.0]
rdf.head()

Restaurant Name Locality  Longitude   Latitude  \
2561        Burger.in  Adchini  77.196923  28.535382   
2562  Days of the Raj  Adchini  77.197475  28.535493   
2563   Dilli Ka Dhaba  Adchini  77.198033  28.537547   
2564        Govardhan  Adchini  77.196924  28.535523   
2565   Mezbaan Grills  Adchini  77.198122  28.538134   

                                 Cuisines  Aggregate rating Rating text  Votes  
2561                            Fast Food               3.2     Average     46  
2562   North Indian, Seafood, Continental               3.4     Average     45  
2563           South Indian, North Indian               2.6     Average     11  
2564  South Indian, North Indian, Chinese               3.4     Average    238  
2565                              Mughlai               3.1     Average      8

## MAP to show restraunts clusters

In [5]:
New_Delhi_Rest = folium.Map(location=[28.52, 77.25], zoom_start=12)

df_Res=rdf
X = df_Res['Latitude']
Y = df_Res['Longitude']
Z = np.stack((X, Y), axis=1)

kmeans = KMeans(n_clusters=5, random_state=0).fit(Z)

clusters = kmeans.labels_
colors = ['red', 'green', 'blue', 'yellow','orange']
df_Res ['Cluster'] = clusters

for latitude, longitude, Locality, cluster in zip(df_Res['Latitude'], df_Res['Longitude'], df_Res['Locality'], df_Res['Cluster']):
    label = folium.Popup(Locality, parse_html=True)
    folium.CircleMarker(
        [latitude, longitude],
        radius=5,
        popup=label,
        color='black',
        fill=True,
        fill_color=colors[cluster],
        fill_opacity=0.7).add_to(New_Delhi_Rest)  

New_Delhi_Rest

## DATA TRANSFORMATION

In [6]:
df_Res_Loc =  df_Res.groupby('Locality').count()['Restaurant Name'].to_frame()
df_Res_rating= df_Res.groupby('Locality')['Aggregate rating'].mean().to_frame()
d_Cuisines = df_Res.groupby(['Locality'])['Cuisines'].agg(', '.join).reset_index()
d_R = df_Res.groupby(['Locality'])['Rating text'].unique().agg(', '.join).reset_index()
d_V = df_Res.groupby(['Locality'])['Votes'].sum().to_frame()
d_Lat = df_Res.groupby('Locality').mean()['Latitude'].to_frame()
d_Lng = df_Res.groupby('Locality').mean()['Longitude'].to_frame()
df_final = pd.merge(d_Lat,d_Lng,on='Locality').merge(df_Res_Loc, on='Locality').merge(d_Cuisines, on='Locality').merge(df_Res_rating,on ='Locality').merge(d_R, on ='Locality').merge(d_V, on ='Locality')
df_final = df_final[df_final['Aggregate rating'] != 0.000000]
df_final.columns =['Locality','Lat','Lng', 'No_of_Restaurant','Cusines', 'Agg_Rating','Comments' ,'No_of_Votes']
df_final.head()

Locality        Lat        Lng  No_of_Restaurant  \
0       ARSS Mall, Paschim Vihar  28.668945  77.101544                 1   
1                        Adchini  28.537063  77.197808                13   
2  Aditya Mega Mall, Karkardooma  28.656131  77.301266                 4   
3                       Aerocity  28.553077  77.104270                 2   
4  Aggarwal City Mall, Pitampura  28.690020  77.134650                 3   

                                             Cusines  Agg_Rating  \
0  North Indian, South Indian, Chinese, Mithai, F...    3.100000   
1  Fast Food, North Indian, Seafood, Continental,...    3.292308   
2  Finger Food, North Indian, Mughlai, Pizza, Fas...    3.275000   
3  Fast Food, Italian, Pizza, North Indian, Conti...    3.200000   
4  North Indian, Chinese, Street Food, Mithai, No...    3.033333   

                         Comments  No_of_Votes  
0                         Average          117  
1  Average, Good, Poor, Very Good         1560  
2                   Average, Good          434  
3                         Average           59  
4                         Average          126

## Define Foursquare Credentials and Find neighbors

In [7]:
CLIENT_ID = '22HDETW15PSK1PVKLJPUL1WDEHFXGPYWSUW2FYILIIMPWK0L' 
CLIENT_SECRET = 'IQLRBG024CVZ1PNJMO5YWRIARZCXDUZ1YUX1GMA2PXPRYWGW' 
VERSION = '20200518' 

def getNearbyVenues(names, latitudes, longitudes, radius=500,LIMIT = 100):
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
        results = requests.get(url).json()["response"]['groups'][0]['items']
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])
    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Locality', 
                  'Locality Latitude', 
                  'Locality Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    return(nearby_venues)

new_Delhi_venues = getNearbyVenues(names=df_final['Locality'],
                                   latitudes=df_final['Lat'],
                                   longitudes=df_final['Lng']
                                  )

ARSS Mall, Paschim Vihar
Adchini
Aditya Mega Mall, Karkardooma
Aerocity
Aggarwal City Mall, Pitampura
Aggarwal City Plaza, Rohini
Alaknanda
Ambience Mall, Vasant Kunj
Anand Lok
Anand Vihar
Andaz Delhi, Aerocity
Ansal Plaza Mall, Khel Gaon Marg
Asaf Ali Road
Ashok Vihar Phase 1
Ashok Vihar Phase 2
Ashok Vihar Phase 3
Barakhamba Road
Basant Lok Market, Vasant Vihar
Bellagio, Ashok Vihar Phase 2
Best Western Taurus Hotel, Mahipalpur
Bhikaji Cama Place
Chanakyapuri
Chander Nagar
Chandni Chowk
Chawri Bazar
Chhatarpur
Chittaranjan Park
City Centre Mall, Rohini
City Square Mall, Rajouri Garden
Civil Lines
Community Centre, New Friends Colony
Connaught Place
Crescent Square Mall, Rohini
Cross River Mall, Karkardooma
Crowne Plaza Hotel, Rohini
Crowne Plaza, Mayur Vihar Phase 1
D Mall, Netaji Subhash Place
DDA Market, Kalu Sarai, Hauz Khas
DLF City Centre Mall, Shalimar Bagh
DLF Emporio Mall, Vasant Kunj
DLF Place Mall, Saket
DLF Promenade Mall, Vasant Kunj
DLF South Square, Sarojini Nagar
Darya

In [9]:
new_Delhi_venues.head()

Locality  Locality Latitude  Locality Longitude  \
0  ARSS Mall, Paschim Vihar          28.668945           77.101544   
1  ARSS Mall, Paschim Vihar          28.668945           77.101544   
2  ARSS Mall, Paschim Vihar          28.668945           77.101544   
3  ARSS Mall, Paschim Vihar          28.668945           77.101544   
4  ARSS Mall, Paschim Vihar          28.668945           77.101544   

                         Venue  Venue Latitude  Venue Longitude  \
0                       Subway       28.669999        77.102546   
1              Café Coffee Day       28.670009        77.102480   
2                    Pizza Hut       28.670321        77.103853   
3  Baljeet's Amritsari Koolcha       28.665768        77.100481   
4                  Little Chef       28.670000        77.101459   

       Venue Category  
0      Sandwich Place  
1         Coffee Shop  
2         Pizza Place  
3   Indian Restaurant  
4  Chinese Restaurant

## Using one hot encoder and grouping data together

In [10]:
# one hot encoding
new_Delhi_onehot = pd.get_dummies(new_Delhi_venues[['Venue Category']], prefix="", prefix_sep="")

# add Locality column back to dataframe
new_Delhi_onehot['Locality'] = new_Delhi_venues['Locality'] 

# move Locality column to the first column
column_list = new_Delhi_onehot.columns.tolist()
column_number = int(column_list.index('Locality'))
column_list = [column_list[column_number]] + column_list[:column_number] + column_list[column_number+1:]
new_Delhi_onehot = new_Delhi_onehot[column_list]
New_Delhi_grouped = new_Delhi_onehot.groupby('Locality').mean().reset_index()
New_Delhi_grouped.head()

Locality       ATM  Accessories Store  Airport  \
0       ARSS Mall, Paschim Vihar  0.111111                0.0      0.0   
1                        Adchini  0.000000                0.0      0.0   
2  Aditya Mega Mall, Karkardooma  0.000000                0.0      0.0   
3                       Aerocity  0.000000                0.0      0.0   
4  Aggarwal City Mall, Pitampura  0.000000                0.0      0.0   

   Airport Food Court  Airport Lounge  Airport Service  Airport Terminal  \
0                 0.0        0.000000              0.0          0.000000   
1                 0.0        0.000000              0.0          0.000000   
2                 0.0        0.000000              0.0          0.000000   
3                 0.0        0.142857              0.0          0.142857   
4                 0.0        0.000000              0.0          0.000000   

   American Restaurant  Arcade  ...  Track Stadium  Trail  Train Station  \
0                  0.0     0.0  ...            0.0    0.0            0.0   
1                  0.0     0.0  ...            0.0    0.0            0.0   
2                  0.0     0.0  ...            0.0    0.0            0.0   
3                  0.0     0.0  ...            0.0    0.0            0.0   
4                  0.0     0.0  ...            0.0    0.0            0.0   

   Turkish Restaurant  Udupi Restaurant  Vegetarian / Vegan Restaurant  \
0                 0.0               0.0                            0.0   
1                 0.0               0.0                            0.0   
2                 0.0               0.0                            0.0   
3                 0.0               0.0                            0.0   
4                 0.0               0.0                            0.0   

   Vietnamese Restaurant  Whisky Bar  Wings Joint  Women's Store  
0                    0.0         0.0          0.0            0.0  
1                    0.0         0.0          0.0            0.0  
2                    0.0         0.0          0.0            0.0  
3                    0.0         0.0          0.0            0.0  
4                    0.0         0.0          0.0            0.0  

[5 rows x 208 columns]

## Create the new dataframe and display the top 10 venues for each Locality.

In [12]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]
num_top_venues = 10
indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Locality']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
Locality_venues_sorted = pd.DataFrame(columns=columns)
Locality_venues_sorted['Locality'] = New_Delhi_grouped['Locality']

for ind in np.arange(New_Delhi_grouped.shape[0]):
    Locality_venues_sorted.iloc[ind, 1:] = return_most_common_venues(New_Delhi_grouped.iloc[ind, :], num_top_venues)

Locality_venues_sorted.head()

Locality 1st Most Common Venue 2nd Most Common Venue  \
0       ARSS Mall, Paschim Vihar     Indian Restaurant        Sandwich Place   
1                        Adchini     Indian Restaurant                  Café   
2  Aditya Mega Mall, Karkardooma     Indian Restaurant           Pizza Place   
3                       Aerocity                 Hotel   Rental Car Location   
4  Aggarwal City Mall, Pitampura      Department Store  Fast Food Restaurant   

  3rd Most Common Venue           4th Most Common Venue  \
0                Market  Multicuisine Indian Restaurant   
1      Parsi Restaurant                             Pub   
2         Shopping Mall                       Multiplex   
3        Airport Lounge                Airport Terminal   
4                  Café              Chinese Restaurant   

         5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0                  Pizza Place           Coffee Shop    Chinese Restaurant   
1                   Restaurant         Women's Store           Fish Market   
2                        Hotel                  Café         Women's Store   
3         Fast Food Restaurant           Coffee Shop           Flea Market   
4  Eastern European Restaurant     Electronics Store                Garden   

  8th Most Common Venue   9th Most Common Venue 10th Most Common Venue  
0                   ATM     American Restaurant             Donut Shop  
1    Frozen Yogurt Shop     Fried Chicken Joint      French Restaurant  
2           Flea Market      Frozen Yogurt Shop    Fried Chicken Joint  
3           Gaming Cafe  Furniture / Home Store     Frozen Yogurt Shop  
4           Gaming Cafe  Furniture / Home Store     Frozen Yogurt Shop

## Clustering the locality

In [13]:
kclusters = 5

New_Delhi_clustering = New_Delhi_grouped.drop('Locality', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(New_Delhi_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 
kmeans.labels_.shape

# add clustering labels
New_Delhi_merged = df_final.head(239)
New_Delhi_merged['Cluster Labels'] = kmeans.labels_

# merge New_Delhi_grouped with df_Chinese to add latitude/longitude for each Locality
New_Delhi_merged = New_Delhi_merged.join(Locality_venues_sorted.set_index('Locality'), on='Locality')

New_Delhi_merged.head()

/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy


Locality        Lat        Lng  No_of_Restaurant  \
0       ARSS Mall, Paschim Vihar  28.668945  77.101544                 1   
1                        Adchini  28.537063  77.197808                13   
2  Aditya Mega Mall, Karkardooma  28.656131  77.301266                 4   
3                       Aerocity  28.553077  77.104270                 2   
4  Aggarwal City Mall, Pitampura  28.690020  77.134650                 3   

                                             Cusines  Agg_Rating  \
0  North Indian, South Indian, Chinese, Mithai, F...    3.100000   
1  Fast Food, North Indian, Seafood, Continental,...    3.292308   
2  Finger Food, North Indian, Mughlai, Pizza, Fas...    3.275000   
3  Fast Food, Italian, Pizza, North Indian, Conti...    3.200000   
4  North Indian, Chinese, Street Food, Mithai, No...    3.033333   

                         Comments  No_of_Votes  Cluster Labels  \
0                         Average          117               0   
1  Average, Good, Poor, Very Good         1560               0   
2                   Average, Good          434               0   
3                         Average           59               1   
4                         Average          126               4   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0     Indian Restaurant        Sandwich Place                Market   
1     Indian Restaurant                  Café      Parsi Restaurant   
2     Indian Restaurant           Pizza Place         Shopping Mall   
3                 Hotel   Rental Car Location        Airport Lounge   
4      Department Store  Fast Food Restaurant                  Café   

            4th Most Common Venue        5th Most Common Venue  \
0  Multicuisine Indian Restaurant                  Pizza Place   
1                             Pub                   Restaurant   
2                       Multiplex                        Hotel   
3                Airport Terminal         Fast Food Restaurant   
4              Chinese Restaurant  Eastern European Restaurant   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0           Coffee Shop    Chinese Restaurant                   ATM   
1         Women's Store           Fish Market    Frozen Yogurt Shop   
2                  Café         Women's Store           Flea Market   
3           Coffee Shop           Flea Market           Gaming Cafe   
4     Electronics Store                Garden           Gaming Cafe   

    9th Most Common Venue 10th Most Common Venue  
0     American Restaurant             Donut Shop  
1     Fried Chicken Joint      French Restaurant  
2      Frozen Yogurt Shop    Fried Chicken Joint  
3  Furniture / Home Store     Frozen Yogurt Shop  
4  Furniture / Home Store     Frozen Yogurt Shop

## Mapping the clusters

In [16]:
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=10)
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
#colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
#rainbow = [colors.rgb2hex(i) for i in colors_array]
colors = ['red', 'green', 'blue', 'yellow','orange']

markers_colors = []
for lat, lon, poi, cluster in zip(New_Delhi_merged['Lat'], New_Delhi_merged['Lng'], New_Delhi_merged['Locality'], New_Delhi_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color='black',
        fill=True,
        fill_color=colors[cluster],
        fill_opacity=0.7).add_to(map_clusters)
map_clusters

## Examining the clusters

In [14]:
New_Delhi_merged.loc[New_Delhi_merged['Cluster Labels'] == 0, New_Delhi_merged.columns[[1] + list(range(5, New_Delhi_merged.shape[1]))]].head()

Lat  Agg_Rating                        Comments  No_of_Votes  \
0   28.668945    3.100000                         Average          117   
1   28.537063    3.292308  Average, Good, Poor, Very Good         1560   
2   28.656131    3.275000                   Average, Good          434   
13  28.690182    3.090000             Average, Good, Poor          971   
14  28.693969    3.378571                   Average, Good         2343   

    Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0                0     Indian Restaurant        Sandwich Place   
1                0     Indian Restaurant                  Café   
2                0     Indian Restaurant           Pizza Place   
13               0     Indian Restaurant            Smoke Shop   
14               0           Pizza Place     Indian Restaurant   

      3rd Most Common Venue           4th Most Common Venue  \
0                    Market  Multicuisine Indian Restaurant   
1          Parsi Restaurant                             Pub   
2             Shopping Mall                       Multiplex   
13              Pizza Place                       BBQ Joint   
14  South Indian Restaurant                  Sandwich Place   

   5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0            Pizza Place           Coffee Shop    Chinese Restaurant   
1             Restaurant         Women's Store           Fish Market   
2                  Hotel                  Café         Women's Store   
13                Market           Snack Place          Dessert Shop   
14           Coffee Shop      Asian Restaurant           Fish Market   

          8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0                           ATM   American Restaurant             Donut Shop  
1            Frozen Yogurt Shop   Fried Chicken Joint      French Restaurant  
2                   Flea Market    Frozen Yogurt Shop    Fried Chicken Joint  
13  Eastern European Restaurant     Food & Drink Shop                 Garden  
14       Furniture / Home Store    Frozen Yogurt Shop    Fried Chicken Joint

In [15]:
New_Delhi_merged.loc[New_Delhi_merged['Cluster Labels'] == 1, New_Delhi_merged.columns[[1] + list(range(5, New_Delhi_merged.shape[1]))]].head()

Lat  Agg_Rating Comments  No_of_Votes  Cluster Labels  \
3   28.553077        3.20  Average           59               1   
10  28.554807        3.00  Average            4               1   
12  28.641698        3.05  Average           17               1   
19  28.548827        2.70  Average            9               1   
25  28.495624        2.70  Average           23               1   

   1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
3                  Hotel   Rental Car Location        Airport Lounge   
10                 Hotel           Coffee Shop     Indian Restaurant   
12                 Hotel         Movie Theater     Indian Restaurant   
19                 Hotel    Italian Restaurant                Buffet   
25   Japanese Restaurant     Indian Restaurant            Donut Shop   

   4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
3       Airport Terminal  Fast Food Restaurant           Coffee Shop   
10  Gym / Fitness Center            Food Court          Cocktail Bar   
12                Hostel           Flea Market                Garden   
19       Bed & Breakfast             Hotel Bar     Indian Restaurant   
25                 Hotel         Women's Store           Flea Market   

   7th Most Common Venue   8th Most Common Venue   9th Most Common Venue  \
3            Flea Market             Gaming Cafe  Furniture / Home Store   
10                Bakery                  Lounge      Punjabi Restaurant   
12           Gaming Cafe  Furniture / Home Store      Frozen Yogurt Shop   
19     Accessories Store             Gaming Cafe  Furniture / Home Store   
25           Gaming Cafe  Furniture / Home Store      Frozen Yogurt Shop   

   10th Most Common Venue  
3      Frozen Yogurt Shop  
10                    Spa  
12    Fried Chicken Joint  
19     Frozen Yogurt Shop  
25    Fried Chicken Joint

In [17]:
New_Delhi_merged.loc[New_Delhi_merged['Cluster Labels'] == 2, New_Delhi_merged.columns[[1] + list(range(5, New_Delhi_merged.shape[1]))]].head()

Lat  Agg_Rating                  Comments  No_of_Votes  \
5    28.700516    3.040000       Average, Good, Poor          594   
15   28.691136    3.390909  Average, Good, Very Good          485   
22   28.654105    3.085714                   Average           80   
57   28.699837    3.376471  Average, Good, Very Good         2460   
101  28.667644    3.300000                   Average          132   

     Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
5                 2  Fast Food Restaurant           Pizza Place   
15                2  Gym / Fitness Center           Pizza Place   
22                2           Pizza Place         Women's Store   
57                2           Pizza Place            Food Truck   
101               2           Pizza Place   American Restaurant   

       3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
5       Gym / Fitness Center         Shopping Mall             Multiplex   
15   South Indian Restaurant  Fast Food Restaurant             BBQ Joint   
22               Flea Market                Garden           Gaming Cafe   
57             Women's Store           Flea Market                Garden   
101              Bus Station         Metro Station  Fast Food Restaurant   

      6th Most Common Venue   7th Most Common Venue   8th Most Common Venue  \
5         Electronics Store          Sandwich Place      Frozen Yogurt Shop   
15                     Food             Gaming Cafe  Furniture / Home Store   
22   Furniture / Home Store      Frozen Yogurt Shop     Fried Chicken Joint   
57              Gaming Cafe  Furniture / Home Store      Frozen Yogurt Shop   
101           Historic Site       Electronics Store      English Restaurant   

    9th Most Common Venue  10th Most Common Venue  
5     Fried Chicken Joint       French Restaurant  
15     Frozen Yogurt Shop     Fried Chicken Joint  
22      French Restaurant              Food Truck  
57    Fried Chicken Joint       French Restaurant  
101           Gaming Cafe  Furniture / Home Store

In [18]:
New_Delhi_merged.loc[New_Delhi_merged['Cluster Labels'] ==3 , New_Delhi_merged.columns[[1] + list(range(5, New_Delhi_merged.shape[1]))]].head()

Lat  Agg_Rating       Comments  No_of_Votes  Cluster Labels  \
55  28.617102    4.200000      Very Good         3010               3   
59  28.654883    3.053846  Average, Good          262               3   

   1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
55     Indian Restaurant         Women's Store           Flea Market   
59     Indian Restaurant         Women's Store           Flea Market   

   4th Most Common Venue 5th Most Common Venue   6th Most Common Venue  \
55                Garden           Gaming Cafe  Furniture / Home Store   
59                Garden           Gaming Cafe  Furniture / Home Store   

   7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
55    Frozen Yogurt Shop   Fried Chicken Joint     French Restaurant   
59    Frozen Yogurt Shop   Fried Chicken Joint     French Restaurant   

   10th Most Common Venue  
55             Food Truck  
59             Food Truck

In [19]:
New_Delhi_merged.loc[New_Delhi_merged['Cluster Labels'] == 4, New_Delhi_merged.columns[[1] + list(range(5, New_Delhi_merged.shape[1]))]].head()

Lat  Agg_Rating                  Comments  No_of_Votes  \
4  28.690020    3.033333                   Average          126   
6  28.527088    3.117391       Average, Good, Poor         1012   
7  28.541298    3.425000  Average, Good, Very Good         2460   
8  28.555599    3.800000        Average, Very Good         2411   
9  28.659870    3.281481             Average, Good         1309   

   Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
4               4      Department Store  Fast Food Restaurant   
6               4                Market    Chinese Restaurant   
7               4           Coffee Shop  Fast Food Restaurant   
8               4               Stadium                  Café   
9               4                  Café                   ATM   

  3rd Most Common Venue 4th Most Common Venue        5th Most Common Venue  \
4                  Café    Chinese Restaurant  Eastern European Restaurant   
6                 Hotel                   Bar                   Steakhouse   
7      Asian Restaurant        Clothing Store           Italian Restaurant   
8          Dessert Shop           Golf Course         Other Great Outdoors   
9          Burger Joint                  Park                Burrito Place   

  6th Most Common Venue 7th Most Common Venue   8th Most Common Venue  \
4     Electronics Store                Garden             Gaming Cafe   
6           Coffee Shop           Gaming Cafe  Furniture / Home Store   
7                  Café         Shopping Mall      Chinese Restaurant   
8           Coffee Shop           Music Venue           Metro Station   
9              Pharmacy             Hotel Bar             Fish Market   

    9th Most Common Venue 10th Most Common Venue  
4  Furniture / Home Store     Frozen Yogurt Shop  
6      Frozen Yogurt Shop    Fried Chicken Joint  
7       Indian Restaurant    Fried Chicken Joint  
8           Women's Store      Food & Drink Shop  
9          Ice Cream Shop    Fried Chicken Joint

## Thank you!